In [103]:
#https://blog.patricktriest.com/analyzing-cryptocurrencies-python/
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
import plotly.express as px
py.init_notebook_mode(connected=True)

In [104]:
def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries'''
    cache_path = '{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(quandl_id))
    except (OSError, IOError) as e:
        print('Downloading {} from Quandl'.format(quandl_id))
        df = quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(quandl_id, cache_path))
    return df

In [105]:
# Pull Kraken BTC price exchange data
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')

Loaded BCHARTS/KRAKENUSD from cache


In [116]:
btc_usd_price_kraken.head(1)

Open       High    Low  Close  Volume (BTC)  \
Date                                                          
2014-01-07  874.6704  892.06753  810.0  810.0     15.622378   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522

In [66]:
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_kraken.index, y=np.log(btc_usd_price_kraken['Weighted Price']))
py.iplot([btc_trace])

In [106]:
# Pull pricing data for 3 more BTC exchanges
exchanges = ['BITSTAMP','ITBIT']

exchange_data = {}

exchange_data['KRAKEN'] = btc_usd_price_kraken

for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    btc_exchange_df = get_quandl_data(exchange_code)
    exchange_data[exchange] = btc_exchange_df

Loaded BCHARTS/BITSTAMPUSD from cache
Loaded BCHARTS/ITBITUSD from cache


In [107]:
def merge_dfs_on_column(dataframes, labels, col):
    '''Merge a single column of each dataframe into a new combined dataframe'''
    series_dict = {}
    for index in range(len(dataframes)):
        series_dict[labels[index]] = dataframes[index][col]
        
    return pd.DataFrame(series_dict)

In [108]:
# Merge the BTC price dataseries' into a single dataframe
btc_usd_datasets = merge_dfs_on_column(list(exchange_data.values()), list(exchange_data.keys()), 'Weighted Price')

In [117]:
def df_scatter(df, title, seperate_y_axis=False, y_axis_label='', scale='linear', initial_hide=False):
    '''Generate a scatter plot of the entire dataframe'''
    label_arr = list(df)
    series_arr = list(map(lambda col: df[col], label_arr))
    layout = go.Layout(title=title, legend=dict(orientation="h"), xaxis=dict(type='date'),
        yaxis=dict(title=y_axis_label, showticklabels= not seperate_y_axis, type=scale)) 
    y_axis_config = dict(overlaying='y', showticklabels=False, type=scale )
    visibility = True
    if initial_hide:
        visibility = 'legendonly'
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(x=series.index, y=np.log(series), name=label_arr[index], visible=True)
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config    
        trace_arr.append(trace)
    fig = go.Figure(data=trace_arr, layout=layout)
    py.iplot(fig)

In [111]:
# Plot all of the BTC exchange prices
df_scatter(btc_usd_datasets, 'Bitcoin Price (USD) By Exchange')

C:\Anaconda3\lib\site-packages\pandas\core\series.py:726: RuntimeWarning:

divide by zero encountered in log



In [112]:
# Remove "0" values
btc_usd_datasets.replace(0, np.nan, inplace=True)

In [114]:
# Calculate the average BTC price as a new column
btc_usd_datasets['avg_btc_price_usd'] = btc_usd_datasets.mean(axis=1)

In [115]:
# Plot the average BTC price
btc_trace = go.Scatter(x=btc_usd_datasets.index, y=np.log(btc_usd_datasets['avg_btc_price_usd']))
py.iplot([btc_trace])

In [76]:
def get_json_data(json_url, cache_path):
    '''Download and cache JSON data, return as a dataframe.'''
    try:        
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(json_url))
    except (OSError, IOError) as e:
        print('Downloading {}'.format(json_url))
        df = pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(json_url, cache_path))
    return df

In [77]:
base_polo_url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date = datetime.strptime('2015-01-01', '%Y-%m-%d') # get data from the start of 2015
end_date = datetime.now() # up until today
pediod = 86400 # pull daily data (86,400 seconds per day)

def get_crypto_data(poloniex_pair):
    '''Retrieve cryptocurrency data from poloniex'''
    json_url = base_polo_url.format(poloniex_pair, start_date.timestamp(), end_date.timestamp(), pediod)
    data_df = get_json_data(json_url, poloniex_pair)
    data_df = data_df.set_index('date')
    return data_df

In [78]:
altcoins = ['ETH','LTC','XRP','ETC','STR','DASH','SC','XMR','XEM']

altcoin_data = {}
for altcoin in altcoins:
    coinpair = 'BTC_{}'.format(altcoin)
    crypto_price_df = get_crypto_data(coinpair)
    altcoin_data[altcoin] = crypto_price_df

Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420066800.0&end=1619033066.416285&period=86400 at BTC_ETH
Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_LTC&start=1420066800.0&end=1619033066.416285&period=86400 at BTC_LTC
Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XRP&start=1420066800.0&end=1619033066.416285&period=86400 at BTC_XRP
Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETC&start=1420066800.0&end=1619033066.416285&period=86400 at BTC_ETC
Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_STR&start=1420066800.0&end=1619033066.416285&period=86400 at BTC_STR
Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_DASH&start=1420066800.0&end=1619033066.416285&period=86400 at BTC_DASH
Cached https://poloniex.com/public?command=returnChartData&currencyPair=BTC_SC&start=1420066800.0&end=1619033066.416285&period=8

In [79]:
altcoin_data['ETH'].tail()

high       low      open     close      volume   quoteVolume  \
date                                                                           
2021-04-17  0.040164  0.038579  0.039477  0.038593  297.820077   7553.647571   
2021-04-18  0.039866  0.036900  0.038593  0.039838  618.533034  16007.583362   
2021-04-19  0.039936  0.038301  0.039819  0.038802  315.930896   8085.317468   
2021-04-20  0.041376  0.038024  0.038891  0.041311  568.498391  14460.287771   
2021-04-21  0.043839  0.041000  0.041314  0.043763  411.250039   9759.787066   

            weightedAverage  
date                         
2021-04-17         0.039427  
2021-04-18         0.038640  
2021-04-19         0.039075  
2021-04-20         0.039314  
2021-04-21         0.042137

In [80]:
# Calculate USD Price as a new column in each altcoin dataframe
for altcoin in altcoin_data.keys():
    altcoin_data[altcoin]['price_usd'] =  altcoin_data[altcoin]['weightedAverage'] * btc_usd_datasets['avg_btc_price_usd']

In [81]:
# Merge USD price of each altcoin into single dataframe 
combined_df = merge_dfs_on_column(list(altcoin_data.values()), list(altcoin_data.keys()), 'price_usd')

In [82]:
# Add BTC price to the dataframe
combined_df['BTC'] = btc_usd_datasets['avg_btc_price_usd']

In [87]:
# Chart all of the altocoin prices
df_scatter(combined_df, 'Cryptocurrency Prices (USD)', seperate_y_axis=False, y_axis_label='Coin Value (USD)') # scale='log'

In [88]:
# Calculate the pearson correlation coefficients for cryptocurrencies in 2016
combined_df_2016 = combined_df[combined_df.index.year == 2016]
combined_df_2016.pct_change().corr(method='pearson')

ETH       LTC       XRP       ETC       STR      DASH        SC  \
ETH   1.000000 -0.064652  0.085630 -0.181991  0.035093  0.122695  0.169642   
LTC  -0.064652  1.000000  0.053712 -0.131079  0.113523 -0.012194  0.012253   
XRP   0.085630  0.053712  1.000000 -0.054095  0.320116  0.088657  0.021098   
ETC  -0.181991 -0.131079 -0.054095  1.000000 -0.102654  0.003992 -0.008066   
STR   0.035093  0.113523  0.320116 -0.102654  1.000000  0.058083  0.143252   
DASH  0.122695 -0.012194  0.088657  0.003992  0.058083  1.000000  0.026602   
SC    0.169642  0.012253  0.021098 -0.008066  0.143252  0.026602  1.000000   
XMR   0.087216  0.129475  0.027649 -0.105898  0.027998  0.121537  0.047910   
XEM   0.043205  0.160667  0.101326 -0.080938  0.225132  0.014571  0.106153   
BTC  -0.006502  0.750174  0.044161 -0.170538  0.079075 -0.014040  0.035116   

           XMR       XEM       BTC  
ETH   0.087216  0.043205 -0.006502  
LTC   0.129475  0.160667  0.750174  
XRP   0.027649  0.101326  0.044161  
ETC  -0.105898 -0.080938 -0.170538  
STR   0.027998  0.225132  0.079075  
DASH  0.121537  0.014571 -0.014040  
SC    0.047910  0.106153  0.035116  
XMR   1.000000  0.016438  0.127520  
XEM   0.016438  1.000000  0.227674  
BTC   0.127520  0.227674  1.000000

In [101]:
def correlation_heatmap(df, title, absolute_bounds=True):
    '''Plot a correlation heatmap for the entire dataframe'''
    heatmap = go.Heatmap(
        z=df.corr(method='pearson').values,
        x=df.columns,
        y=df.columns,
        colorbar=dict(title='Pearson Coefficient'),
    )
    
    layout = go.Layout(title=title)
    
    if absolute_bounds:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
        
    fig = go.Figure(data=[heatmap], layout=layout)
    py.iplot(fig)

In [102]:
correlation_heatmap(combined_df_2016.pct_change(), "Cryptocurrency Correlations in 2016")